In [2]:
# unzip input file first

import xml.etree.ElementTree as ET
import requests
import math
import pprint
import time
import numpy as np
import pandas as pd

## Travis County Boundary API

In [3]:
response = requests.get("https://geo.traviscountytx.gov/arcgis/rest/services/TNR/TravisCountyBoundary/MapServer/0/query?where=1%3D1&outFields=*&outSR=4326&f=json")


In [4]:
boundary = response.json()['features'][0]['geometry']['paths'][0]
pprint.pprint(boundary[0])

[-98.02690146055397, 30.25180859020622]


In [5]:
latitudes = []
longitudes = []

for coord in boundary:
    longitudes.append(coord[0])
    latitudes.append(coord[1])
    
print(len(longitudes))
print(len(latitudes))

213
213


## Region Mapping

In [6]:
LATITUDE_MILES = 69
LONGITUDE_MILES = 54.6

vertical_distance = (max(latitudes) - min(latitudes))*LATITUDE_MILES
horizontal_distance = (max(longitudes) - min(longitudes))*LONGITUDE_MILES

In [7]:
# Assuming we want to make 400 squares, how should we partition the vertically/horizontally
NUM_REGIONS = 400
square_len = (vertical_distance*horizontal_distance/NUM_REGIONS)**0.5

In [8]:
latitude_delta = square_len/LATITUDE_MILES
longitude_delta = square_len/LONGITUDE_MILES
longitude_delta

0.03918197759635523

In [9]:
lat_lon = zip(latitudes, longitudes)

In [10]:
min_lat = min(latitudes)
min_lon = min(longitudes)
max_lat = max(latitudes)
max_lon = max(longitudes)
nrows = math.ceil((max_lat - min_lat) / latitude_delta)
ncols = math.ceil((max_lon - min_lon) / longitude_delta)
def map_point_to_region(latitude, longitude):
    return math.floor((latitude-min_lat)/latitude_delta) * ncols  + math.floor((longitude-min_lon)/longitude_delta)

In [11]:
def get_representative(region_num): # 8 cols per row, # R10 --> row_num = 1, col_num = 2
    row_num = region_num//ncols # Correct
    col_num = region_num - row_num*ncols
    lat = min_lat + row_num * latitude_delta + 0.5*latitude_delta
    lon = min_lon + col_num * longitude_delta + 0.5*longitude_delta
    return [lon, lat]

In [12]:
map_point_to_region(30.084446, -97.702885)

33

In [13]:
get_representative(13)

[-97.6441785574555, 30.038787023039202]

In [14]:
region_coords = [get_representative(i) for i in range(400)]
pprint.pprint(region_coords)

[[-98.15354426620812, 30.038787023039202],
 [-98.11436228861176, 30.038787023039202],
 [-98.0751803110154, 30.038787023039202],
 [-98.03599833341904, 30.038787023039202],
 [-97.99681635582269, 30.038787023039202],
 [-97.95763437822635, 30.038787023039202],
 [-97.91845240062999, 30.038787023039202],
 [-97.87927042303363, 30.038787023039202],
 [-97.84008844543727, 30.038787023039202],
 [-97.80090646784092, 30.038787023039202],
 [-97.76172449024456, 30.038787023039202],
 [-97.7225425126482, 30.038787023039202],
 [-97.68336053505185, 30.038787023039202],
 [-97.6441785574555, 30.038787023039202],
 [-97.60499657985915, 30.038787023039202],
 [-97.56581460226279, 30.038787023039202],
 [-97.52663262466643, 30.038787023039202],
 [-97.48745064707008, 30.038787023039202],
 [-97.44826866947372, 30.038787023039202],
 [-97.40908669187736, 30.038787023039202],
 [-97.369904714281, 30.038787023039202],
 [-98.15354426620812, 30.069791892267624],
 [-98.11436228861176, 30.069791892267624],
 [-98.0751803110

## EMS Stations

In [15]:
# Read in data
ems_data = pd.read_excel("ems_facilities_2020Aug12.xlsx")
print(ems_data.shape)

# Filter data
facility_type = ['Medic Station', 'Demand Medic Station']
ems_data = ems_data[ems_data['FACILITY_TYPE'].isin(facility_type)]
print(ems_data.shape)

# Get coords
ems_longitudes = ems_data['LONGITUDE']
ems_latitudes = ems_data['LATITUDE']

ems_coords = [list(c) for c in zip(ems_longitudes, ems_latitudes)]
pprint.pprint(ems_coords)

(51, 30)
(44, 30)
[[-97.7217247499999, 30.25948737],
 [-97.8602694099999, 30.15636358],
 [-97.7503950699999, 30.24662518],
 [-97.6615917999999, 30.32339149],
 [-97.7482999999999, 30.265327],
 [-97.7259999999999, 30.326725],
 [-97.9295778989999, 30.39848581],
 [-97.7678132899999, 30.22977355],
 [-97.8054399999999, 30.206495],
 [-97.7343149999999, 30.274637],
 [-97.6842324899999, 30.27824902],
 [-97.7264146799999, 30.32672533],
 [-97.7394194699999, 30.26582831],
 [-97.7231080899999, 30.37236405],
 [-97.7588594799999, 30.33455506],
 [-97.9348469179999, 30.302810828],
 [-97.7427673899999, 30.41819953],
 [-97.8535901899999, 30.22782184],
 [-97.7132197299999, 30.2292149],
 [-97.6784999999999, 30.35271081],
 [-97.6895245299999, 30.32525961],
 [-97.7936091899999, 30.17470861],
 [-97.8368195599999, 30.40433212],
 [-97.7725225199999, 30.27734164],
 [-97.6923538799999, 30.38399792],
 [-97.8018875799999, 30.44651026],
 [-97.8239838099999, 30.13933909],
 [-97.8200249299999, 30.27945028],
 [-98.0006

## Hospital Locations

In [16]:
BingMapsKey = "AgmNkDXiPX65nDUv6MUa0gRtHyrrGAMuD5n8mNQfl72ISI6xGZA37clQ0OcP56y-"

# Example
call = requests.get("https://dev.virtualearth.net/REST/v1/LocalSearch/?query=hospital&userLocation=47.602038,-122.333964&key=" + BingMapsKey)
pprint.pprint(call.json())

{'authenticationResultCode': 'ValidCredentials',
 'brandLogoUri': 'http://dev.virtualearth.net/Branding/logo_powered_by.png',
 'copyright': 'Copyright © 2020 Microsoft and its suppliers. All rights '
              'reserved. This API cannot be accessed and the content and any '
              'results may not be used, reproduced or transmitted in any '
              'manner without express written permission from Microsoft '
              'Corporation.',
 'resourceSets': [{'estimatedTotal': 10,
                   'resources': [{'Address': {'addressLine': '1100 9th Ave',
                                              'adminDistrict': 'WA',
                                              'countryRegion': 'US',
                                              'formattedAddress': '1100 9th '
                                                                  'Ave, '
                                                                  'Seattle, '
                                                        

In [53]:
query = "hospital"

# Need to negate second coordinate
area = "30.2672,97.7431"
#29.7604,-95.3698

#call = requests.get("https://dev.virtualearth.net/REST/v1/LocalSearch/?query=" + query + "&userLocation=" + area + "&key=" + BingMapsKey)
#call = requests.get("https://dev.virtualearth.net/REST/v1/LocalSearch/?query=coffee&userLocation=30.2672,97.7431&key=" + BingMapsKey)

call = requests.get("https://dev.virtualearth.net/REST/v1/LocalSearch/?type=Hospitals&userLocation=30.2672,-97.7431&maxResults=25&key=" + BingMapsKey)
#call = requests.get("https://dev.virtualearth.net/REST/v1/LocalSearch/?query=hospital&userLocation=30.2672,-97.7431&maxResults=25&key=" + BingMapsKey)

pprint.pprint(call.json())

{'authenticationResultCode': 'ValidCredentials',
 'brandLogoUri': 'http://dev.virtualearth.net/Branding/logo_powered_by.png',
 'copyright': 'Copyright © 2020 Microsoft and its suppliers. All rights '
              'reserved. This API cannot be accessed and the content and any '
              'results may not be used, reproduced or transmitted in any '
              'manner without express written permission from Microsoft '
              'Corporation.',
 'resourceSets': [{'estimatedTotal': 23,
                   'resources': [{'Address': {'addressLine': '4534 W Gate Blvd '
                                                             'Ste 100',
                                              'adminDistrict': 'TX',
                                              'countryRegion': 'US',
                                              'formattedAddress': '4534 W Gate '
                                                                  'Blvd Ste '
                                                   

In [54]:
hospitals = call.json()['resourceSets'][0]['resources']

#pprint.pprint(hospitals)
print(hospitals[1]['point']['coordinates'])
print(hospitals[1]['name'])

[30.289552688598633, -97.7254867553711]
St. David's Medical Center


In [55]:
# Extract hosipital info
hospital_coords = []
hospital_names = []

for h in hospitals:
    name = h['name']
    hospital_names.append(name)
    
    coord = h['point']['coordinates']
    flipped_coord = [coord[1], coord[0]]
    hospital_coords.append(flipped_coord)

    
pprint.pprint(hospital_coords)
pprint.pprint(hospital_names)


[[-97.80217742919922, 30.23080062866211],
 [-97.7254867553711, 30.289552688598633],
 [-97.77751159667969, 30.247257232666016],
 [-97.70735931396484, 30.303455352783203],
 [-97.74598693847656, 30.305269241333008],
 [-97.77456665039062, 30.226062774658203],
 [-97.68097686767578, 30.61981201171875],
 [-97.80033111572266, 30.17304229736328],
 [-97.6845932006836, 30.332632064819336],
 [-97.76057434082031, 30.3754825592041],
 [-97.7340087890625, 30.276609420776367],
 [-97.62997436523438, 30.444177627563477],
 [-97.74533081054688, 30.281185150146484],
 [-97.7745132446289, 30.223644256591797],
 [-97.75154113769531, 30.278207778930664],
 [-97.36377716064453, 31.077917098999023],
 [-97.70702362060547, 30.305355072021484],
 [-97.70703125, 30.305356979370117],
 [-97.79949188232422, 30.21432113647461],
 [-97.73754119873047, 30.272905349731445],
 [-97.73766326904297, 30.272655487060547],
 [-97.73271942138672, 30.273733139038086],
 [-97.75113677978516, 30.35066795349121]]
['Westgate Pet & Bird Hospit

In [57]:
# Filter hospitals by cleaning search results

i = len(hospital_names) - 1

while(i >= 0):
    name =  hospital_names[i]
    
    # Remove animal hospitals
    if("Animal" in name or "Veterinary" in name or "Pet" in name):
        del hospital_names[i]
        del hospital_coords[i]

    # Remove specialized facilities
    if("Education" in name or "Disorder" in name or "Birth" in name):
        del hospital_names[i]
        del hospital_coords[i]

    i -= 1
    
pprint.pprint(len(hospital_coords))
pprint.pprint(hospital_names)

11
["St. David's Medical Center",
 "Dell Children's Medical Center",
 'Ascension Seton Medical Center Austin',
 "St. David's South Austin Medical Center",
 'Dell Seton Medical Center at The University of Texas',
 'Austin Regional Clinic: ARC South OB',
 'Baylor Scott & White Medical Center - Temple',
 "Dell Children's Blood & Cancer Center",
 'Strictly Pediatrics Surgery Center',
 'University Of Texas Physicians-Downtown Austin',
 'Northwest Hill Surgical Hospital']


## Batch calls of distance matrix

In [58]:
# Prepare data for api call

#locations = region_coords
locations = region_coords + ems_coords + hospital_coords
durations = []

#pprint.pprint(locations)
print(len(locations))

455


In [59]:
batch_size = 7
num_batches = math.ceil(len(locations) / batch_size)
remainder = len(locations) % batch_size

print(num_batches)

65


In [60]:
headers = {
    'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
    'Authorization': '5b3ce3597851110001cf624884518d9d4075408e95e3401165976247',
    'Content-Type': 'application/json; charset=utf-8'
}

In [61]:
for i in range(num_batches):
    print("batch ", i)
    start = i * batch_size
    sources = list(range(start, start + batch_size))
    
    # handle last partial batch
    if(sources[batch_size - 1] >= len(locations)):
        sources = sources[:remainder]
    
    body = {"locations": locations, "sources": sources}
    call = requests.post('https://api.openrouteservice.org/v2/matrix/driving-car', json=body, headers=headers)
    
    duration_batch = call.json()['durations']
    for j in range(len(duration_batch)):
        durations.append(duration_batch[j])
        
    time.sleep(2)
    
pprint.pprint(durations)


batch  0
batch  1
batch  2
batch  3
batch  4
batch  5
batch  6
batch  7
batch  8
batch  9
batch  10
batch  11
batch  12
batch  13
batch  14
batch  15
batch  16
batch  17
batch  18
batch  19
batch  20
batch  21
batch  22
batch  23
batch  24
batch  25
batch  26
batch  27
batch  28
batch  29
batch  30
batch  31
batch  32
batch  33
batch  34
batch  35
batch  36
batch  37
batch  38
batch  39
batch  40
batch  41
batch  42
batch  43
batch  44
batch  45
batch  46
batch  47
batch  48
batch  49
batch  50
batch  51
batch  52
batch  53
batch  54
batch  55
batch  56
batch  57
batch  58
batch  59
batch  60
batch  61
batch  62
batch  63
batch  64
[[0.0,
  1013.54,
  1948.63,
  1674.0,
  1947.58,
  2181.35,
  2426.57,
  2938.03,
  3332.13,
  3506.2,
  3785.73,
  4171.29,
  4240.72,
  4468.86,
  4720.37,
  4981.55,
  5298.91,
  5826.5,
  5397.01,
  5780.25,
  6328.0,
  2265.14,
  1945.11,
  1759.46,
  2736.43,
  2199.44,
  4392.36,
  3611.58,
  3095.92,
  3549.7,
  3504.82,
  4098.08,
  3939.92,
  4361

  2230.44,
  1157.37,
  1054.25,
  1106.97,
  773.91,
  997.95,
  1132.7,
  1296.55,
  1444.31,
  1748.95,
  2449.79,
  2266.03,
  2336.68,
  2179.45,
  2714.8,
  2795.62,
  3271.47,
  2963.71,
  3073.6,
  2024.82,
  2111.31,
  2718.87,
  2353.33,
  1552.08,
  1376.91,
  871.54,
  1334.69,
  1489.87,
  1372.24,
  1627.9,
  1814.47,
  2176.01,
  3805.26,
  2665.64,
  2316.79,
  2619.01,
  2784.36,
  3263.76,
  2932.81,
  2392.04,
  2564.7,
  2633.6,
  1871.74,
  1802.03,
  1301.0,
  1611.77,
  1111.17,
  1212.13,
  1513.39,
  1542.47,
  1665.08,
  1692.59,
  2471.29,
  2232.62,
  2592.01,
  2767.0,
  3144.99,
  4060.54,
  3122.27,
  3170.89,
  2801.41,
  2533.05,
  2410.24,
  2863.13,
  2032.74,
  1562.2,
  1494.42,
  1327.91,
  1192.13,
  1368.56,
  1612.46,
  1720.14,
  1786.02,
  1847.87,
  2194.3,
  3101.37,
  3228.86,
  3150.95,
  3542.09,
  3056.33,
  3109.73,
  2851.71,
  3063.17,
  2697.85,
  2229.45,
  2266.55,
  1916.42,
  1736.76,
  1474.15,
  1346.17,
  1460.83,
  1766.3,
  

  4059.0,
  4030.82,
  3990.97,
  3079.56,
  3099.43,
  2801.35,
  2852.68,
  2698.66,
  2544.39,
  2368.18,
  2236.59,
  2128.45,
  1952.22,
  2669.98,
  3338.24,
  2848.1,
  2792.6,
  2884.56,
  6274.01,
  5715.17,
  4787.41,
  4277.47,
  3734.68,
  3550.37,
  3458.46,
  3035.25,
  3040.86,
  3315.88,
  2889.83,
  2747.59,
  2681.71,
  2528.78,
  2423.75,
  2193.95,
  2936.88,
  3297.64,
  3122.67,
  2855.23,
  3037.08,
  5047.13,
  4909.14,
  4285.58,
  4115.68,
  3965.19,
  3901.8,
  4408.77,
  4581.23,
  3747.25,
  3005.09,
  3220.52,
  2732.8,
  2862.61,
  2595.6,
  2509.27,
  2246.27,
  2405.14,
  2598.04,
  2789.66,
  2865.89,
  2992.64,
  5834.1,
  5250.88,
  4332.8,
  4429.89,
  5954.73,
  4202.69,
  4342.56,
  4092.6,
  3837.26,
  3282.53,
  3136.83,
  2825.04,
  2894.29,
  2689.22,
  2444.29,
  2672.1,
  2560.78,
  2902.16,
  2954.62,
  3202.01,
  3210.1,
  5049.04,
  4477.79,
  4645.44,
  4886.91,
  5106.96,
  5778.69,
  4405.11,
  4213.65,
  3857.23,
  3359.06,
  3153.97,

  1532.87,
  1564.06,
  1759.95,
  2523.04,
  3014.92,
  2710.7,
  2829.32,
  3083.51,
  3370.16,
  3376.6,
  3446.16,
  3526.2,
  3740.06,
  3801.92,
  4148.35,
  5055.42,
  5340.52,
  5264.49,
  5726.5,
  1787.79,
  1841.19,
  1583.18,
  2287.37,
  2317.64,
  1956.37,
  2311.34,
  2481.49,
  2699.15,
  2936.21,
  3015.95,
  3380.9,
  3572.37,
  3717.42,
  3890.71,
  4315.88,
  5376.44,
  4876.09,
  5252.62,
  5301.2,
  5613.46,
  2057.07,
  2132.08,
  1889.65,
  2189.1,
  2936.99,
  3079.62,
  2351.59,
  2744.97,
  3151.44,
  2832.73,
  3108.36,
  3427.82,
  3691.44,
  4364.42,
  3913.38,
  4487.68,
  4493.31,
  4883.79,
  5865.65,
  5512.83,
  6647.72,
  2929.33,
  2643.16,
  2427.49,
  2378.06,
  2696.96,
  3353.91,
  2584.76,
  2964.24,
  3296.13,
  3347.46,
  3111.63,
  3467.48,
  3716.49,
  4001.07,
  4127.2,
  3992.96,
  4710.72,
  5378.97,
  5379.87,
  5675.51,
  5426.93,
  3891.08,
  3682.82,
  2755.06,
  3541.79,
  2919.55,
  2939.0,
  3119.21,
  3062.21,
  3317.0,
  3810.66

  2966.17,
  3095.12,
  3163.47,
  3392.91,
  3554.76,
  5949.72,
  5245.35,
  4676.28,
  5314.28,
  4968.3,
  4474.81,
  3278.6,
  3246.23,
  2930.36,
  2983.42,
  3132.84,
  2911.65,
  2722.07,
  3203.68,
  3060.65,
  3086.15,
  3119.9,
  3507.64,
  3454.41,
  3562.98,
  3831.48,
  6379.64,
  1240.78,
  1047.3,
  1133.78,
  1679.19,
  1289.59,
  1601.78,
  2922.84,
  1002.79,
  1116.11,
  1182.47,
  1514.77,
  1600.24,
  1169.85,
  1675.69,
  1767.58,
  2072.28,
  1956.47,
  1378.07,
  1309.06,
  1699.82,
  1613.08,
  792.36,
  2509.4,
  1491.43,
  1850.62,
  2262.74,
  826.76,
  1382.99,
  4238.96,
  2050.6,
  860.64,
  3345.18,
  2821.49,
  2586.11,
  993.86,
  1930.31,
  1382.28,
  1256.58,
  1822.89,
  1416.72,
  2417.47,
  1887.54,
  1211.3,
  1664.73,
  1266.67,
  1370.57,
  1612.06,
  1150.59,
  1181.74,
  1101.03,
  5079.33,
  1347.39,
  1347.25,
  1207.76,
  1792.05],
 [4080.27,
  3314.13,
  3873.17,
  2406.32,
  2132.72,
  1898.92,
  1653.7,
  1231.11,
  1211.41,
  890.61,


...

  1155.15,
  1330.07,
  1164.23,
  774.69,
  1111.88,
  1061.43,
  1252.86,
  1260.74,
  1665.97,
  1689.76,
  1667.83,
  1901.1,
  1822.54,
  2394.59,
  2155.92,
  2515.31,
  2690.3,
  3227.79,
  4214.21,
  1417.86,
  1466.48,
  977.64,
  656.4,
  533.59,
  1072.35,
  1245.95,
  679.95,
  798.57,
  1052.76,
  1339.41,
  1345.85,
  1415.41,
  1495.45,
  1709.32,
  1771.17,
  2117.6,
  3024.67,
  3309.77,
  3233.74,
  3695.76,
  1351.92,
  1405.32,
  1142.37,
  1186.51,
  781.68,
  313.28,
  350.38,
  450.74,
  668.4,
  905.46,
  985.2,
  1350.16,
  1541.62,
  1686.67,
  1859.96,
  2285.14,
  3345.7,
  2845.34,
  3221.87,
  3270.45,
  3582.71,
  1621.2,
  1391.21,
  1103.19,
  1184.87,
  1293.9,
  973.85,
  205.32,
  641.93,
  1120.69,
  801.98,
  1077.61,
  1397.07,
  1660.69,
  2333.67,
  1882.64,
  2456.93,
  2462.56,
  2853.04,
  3834.9,
  3482.09,
  4616.97,
  2493.46,
  1856.71,
  1641.03,
  1417.93,
  1389.74,
  1349.89,
  438.49,
  845.96,
  1265.38,
  1316.71,
  1080.88,
  1436

  1547.2,
  1691.79,
  1895.91,
  2093.56,
  2333.84,
  4423.46,
  4120.27,
  4531.23,
  4139.45,
  None,
  2931.51,
  2443.27,
  2342.39,
  1898.67,
  1862.98,
  2111.27,
  1994.16,
  1612.85,
  1772.87,
  1563.65,
  1370.5,
  1519.47,
  1648.43,
  1716.78,
  1946.21,
  2108.06,
  5000.17,
  4295.8,
  3726.73,
  4364.73,
  4018.75,
  3525.26,
  2329.05,
  2296.68,
  1980.81,
  2033.87,
  2205.18,
  1992.67,
  1803.08,
  1945.75,
  1613.95,
  1639.45,
  1673.21,
  2060.94,
  2007.72,
  2116.29,
  2384.78,
  5430.09,
  1056.9,
  1997.89,
  1142.64,
  443.81,
  1044.21,
  676.5,
  2453.03,
  1272.98,
  1566.23,
  877.32,
  862.53,
  674.96,
  935.23,
  726.14,
  1036.17,
  2342.47,
  1006.92,
  1648.26,
  1164.8,
  623.22,
  581.97,
  1489.23,
  1878.12,
  1281.06,
  900.59,
  1313.19,
  1726.77,
  1591.49,
  3289.41,
  482.03,
  1691.28,
  2395.63,
  3047.84,
  2736.36,
  1461.0,
  622.92,
  1144.31,
  1909.14,
  2093.07,
  861.25,
  1467.92,
  0.0,
  1108.11,
  816.07,
  787.68,
  780.

  2720.78,
  1465.33,
  1711.11,
  1207.35,
  1522.97,
  1843.82,
  1802.83,
  2007.22,
  1995.34,
  2191.54,
  3614.15,
  2474.53,
  2162.04,
  2587.39,
  2823.61,
  2853.14,
  2707.83,
  2300.48,
  2362.6,
  2309.56,
  1504.66,
  1434.95,
  1339.03,
  1555.48,
  1185.17,
  1438.61,
  1462.39,
  1535.09,
  1786.69,
  1708.12,
  2280.17,
  2041.51,
  2400.9,
  2575.88,
  3113.37,
  4099.79,
  2563.19,
  2611.81,
  2122.97,
  1801.73,
  1678.92,
  2217.68,
  1665.66,
  1019.34,
  1029.77,
  1188.41,
  1112.04,
  1247.16,
  1266.74,
  1381.04,
  1594.9,
  1656.75,
  2003.18,
  2910.25,
  2921.0,
  3119.33,
  3064.51,
  2497.25,
  2550.65,
  2287.7,
  2331.85,
  1927.01,
  1458.61,
  1495.71,
  1141.04,
  880.67,
  850.25,
  926.35,
  974.76,
  1076.49,
  1572.26,
  1697.16,
  1896.37,
  3231.28,
  2456.57,
  2833.1,
  2882.69,
  2970.68,
  2766.53,
  2536.54,
  2248.53,
  2330.2,
  2439.23,
  2293.27,
  1361.64,
  1114.39,
  1280.74,
  689.28,
  726.22,
  742.03,
  944.45,
  2127.63,
  1

  3654.06,
  3861.4,
  3835.78,
  4260.12,
  4209.13,
  4550.5,
  4602.96,
  4850.35,
  4862.05,
  7016.57,
  6445.33,
  6612.98,
  6854.44,
  6992.97,
  5765.88,
  5254.47,
  4901.29,
  4400.85,
  4168.51,
  4055.07,
  3715.54,
  3699.14,
  3729.29,
  3882.47,
  3690.69,
  4509.75,
  4450.99,
  4952.51,
  5069.01,
  4706.51,
  6824.4,
  7053.56,
  7001.58,
  6860.33,
  5364.78,
  5668.69,
  4719.46,
  4412.77,
  4188.1,
  3956.86,
  3879.53,
  3618.06,
  3465.52,
  3505.97,
  3671.62,
  3622.46,
  3759.2,
  4259.73,
  4596.48,
  5053.69,
  5033.29,
  6994.82,
  7402.95,
  6762.33,
  7116.83,
  4983.97,
  4681.1,
  5091.41,
  4498.08,
  3926.37,
  3688.48,
  3554.84,
  3621.62,
  3439.74,
  3474.8,
  3642.15,
  3627.97,
  4104.17,
  4219.47,
  3981.15,
  4205.0,
  4716.17,
  7486.52,
  6534.23,
  6145.67,
  5281.6,
  5059.17,
  5274.3,
  4239.18,
  4209.4,
  3783.89,
  3596.6,
  3619.06,
  3552.23,
  3486.67,
  3510.76,
  3562.94,
  3379.21,
  3596.75,
  3820.75,
  4076.38,
  4274.5,
 

  543.92,
  884.18,
  1286.01,
  809.29,
  764.7,
  1322.85,
  1241.79,
  455.57,
  721.22,
  850.19,
  1532.14,
  752.18,
  2826.42,
  1211.92,
  1927.96,
  1932.63,
  2286.04,
  1974.57,
  1250.23,
  1081.25,
  1380.23,
  1069.82,
  1328.99,
  792.75,
  1004.92,
  1048.86,
  1669.96,
  1572.33,
  682.4,
  771.78,
  449.71,
  872.1,
  719.84,
  841.85,
  3887.69,
  748.59,
  748.46,
  703.06,
  0.0]]


In [30]:
print(len(durations), len(durations[0]))

467 467


In [31]:
np.savetxt("durations3.csv", np.array(durations), delimiter=",", fmt="%s")